In [69]:
import yfinance as yf
import pandas as pd

ticker = 'AAPL'
data = yf.Ticker(ticker)

hist = data.history(period='max', auto_adjust=True)
df = pd.DataFrame(hist).reset_index()
df

Date        Open        High         Low       Close     Volume  \
0     1980-12-12    0.100751    0.101189    0.100751    0.100751  469033600   
1     1980-12-15    0.095933    0.095933    0.095495    0.095495  175884800   
2     1980-12-16    0.088923    0.088923    0.088485    0.088485  105728000   
3     1980-12-17    0.090676    0.091114    0.090676    0.090676   86441600   
4     1980-12-18    0.093304    0.093742    0.093304    0.093304   73449600   
...          ...         ...         ...         ...         ...        ...   
10198 2021-05-25  127.820000  128.320007  126.320000  126.900002   72009500   
10199 2021-05-26  126.959999  127.389999  126.419998  126.849998   56575900   
10200 2021-05-27  126.440002  127.639999  125.080002  125.279999   94625600   
10201 2021-05-28  125.570000  125.800003  124.550003  124.610001   71311100   
10202 2021-06-01  125.080002  125.349998  123.940002  124.279999   67500600   

       Dividends  Stock Splits  
0            0.0           0.0  
1            0.0           0.0  
2            0.0           0.0  
3            0.0           0.0  
4            0.0           0.0  
...          ...           ...  
10198        0.0           0.0  
10199        0.0           0.0  
10200        0.0           0.0  
10201        0.0           0.0  
10202        0.0           0.0  

[10203 rows x 8 columns]

In [70]:
import pandas as pd
df = df.rename(columns={'Date':'ds', 'Close':'y'})
# df = pd.DataFrame()

# df['ds'] = hist.index
# df['y'] = hist.Close.values
df.head()

ds      Open      High       Low         y     Volume  Dividends  \
0 1980-12-12  0.100751  0.101189  0.100751  0.100751  469033600        0.0   
1 1980-12-15  0.095933  0.095933  0.095495  0.095495  175884800        0.0   
2 1980-12-16  0.088923  0.088923  0.088485  0.088485  105728000        0.0   
3 1980-12-17  0.090676  0.091114  0.090676  0.090676   86441600        0.0   
4 1980-12-18  0.093304  0.093742  0.093304  0.093304   73449600        0.0   

   Stock Splits  
0           0.0  
1           0.0  
2           0.0  
3           0.0  
4           0.0

In [71]:
from prophet import Prophet

m = Prophet(daily_seasonality=False)
# m = Prophet()

m.fit(df)

In [72]:
future = m.make_future_dataframe(365, freq='D')
forecast = m.predict(future)

In [73]:
forecast.head()

ds     trend  yhat_lower  yhat_upper  trend_lower  trend_upper  \
0 1980-12-12  0.111845   -9.228719    9.720263     0.111845     0.111845   
1 1980-12-15  0.111944   -9.132190   10.481438     0.111944     0.111944   
2 1980-12-16  0.111977   -9.002273   10.500743     0.111977     0.111977   
3 1980-12-17  0.112010   -9.573034   10.267969     0.112010     0.112010   
4 1980-12-18  0.112043   -8.965490   10.938296     0.112043     0.112043   

   additive_terms  additive_terms_lower  additive_terms_upper    weekly  \
0        0.022796              0.022796              0.022796 -0.063862   
1        0.141912              0.141912              0.141912  0.027688   
2        0.152746              0.152746              0.152746  0.028441   
3        0.147644              0.147644              0.147644  0.013199   
4        0.149432              0.149432              0.149432  0.005029   

   weekly_lower  weekly_upper    yearly  yearly_lower  yearly_upper  \
0     -0.063862     -0.063862  0.086658      0.086658      0.086658   
1      0.027688      0.027688  0.114224      0.114224      0.114224   
2      0.028441      0.028441  0.124305      0.124305      0.124305   
3      0.013199      0.013199  0.134444      0.134444      0.134444   
4      0.005029      0.005029  0.144404      0.144404      0.144404   

   multiplicative_terms  multiplicative_terms_lower  \
0                   0.0                         0.0   
1                   0.0                         0.0   
2                   0.0                         0.0   
3                   0.0                         0.0   
4                   0.0                         0.0   

   multiplicative_terms_upper      yhat  
0                         0.0  0.134642  
1                         0.0  0.253857  
2                         0.0  0.264723  
3                         0.0  0.259654  
4                         0.0  0.261476

In [81]:
forecast[['ds', 'yhat','yhat_lower', 'yhat_upper']].tail()

ds       yhat  yhat_lower  yhat_upper
10563 2022-05-28  99.274758   89.399014  108.769594
10564 2022-05-29  99.260821   89.058044  109.479461
10565 2022-05-30  99.277792   90.329202  108.909878
10566 2022-05-31  99.260976   89.295828  108.866715
10567 2022-06-01  99.227029   88.559793  108.675617

In [109]:
# fig1 = m.plot(forecast);

In [106]:
from prophet.plot import plot_plotly, plot_components_plotly

plot_plotly(m, forecast);

In [107]:
plot_components_plotly(m, forecast);

## Make function

In [99]:
import yfinance as yf
import pandas as pd
from prophet import Prophet
from prophet.plot import plot_plotly, plot_components_plotly




def show_ticker(ticker, period='max'):
    
    # pull market data from yahoo finance
    data = yf.Ticker(ticker)
    hist = data.history(period, auto_adjust=True)
    # convert it to dataframe
    df = pd.DataFrame(hist).reset_index()

    return df

def make_forecast(ticker, periods):
    # prepare for prophet to run
    df = show_ticker(ticker)
    df_re = df.rename(columns={'Date' : 'ds', 'Close' : 'y'})
    m = Prophet(daily_seasonality=False)
    m.fit(df_re)
    future = m.make_future_dataframe(365, freq='D')
    forecast = m.predict(future)
    
    return m, forecast


In [93]:
prep_ticker('AAPL')

Date        Open        High         Low       Close     Volume  \
0     1980-12-12    0.100751    0.101189    0.100751    0.100751  469033600   
1     1980-12-15    0.095933    0.095933    0.095495    0.095495  175884800   
2     1980-12-16    0.088923    0.088923    0.088485    0.088485  105728000   
3     1980-12-17    0.090676    0.091114    0.090676    0.090676   86441600   
4     1980-12-18    0.093304    0.093742    0.093304    0.093304   73449600   
...          ...         ...         ...         ...         ...        ...   
10198 2021-05-25  127.820000  128.320007  126.320000  126.900002   72009500   
10199 2021-05-26  126.959999  127.389999  126.419998  126.849998   56575900   
10200 2021-05-27  126.440002  127.639999  125.080002  125.279999   94625600   
10201 2021-05-28  125.570000  125.800003  124.550003  124.610001   71311100   
10202 2021-06-01  125.080002  125.349998  123.940002  124.279999   67500600   

       Dividends  Stock Splits  
0            0.0           0.0  
1            0.0           0.0  
2            0.0           0.0  
3            0.0           0.0  
4            0.0           0.0  
...          ...           ...  
10198        0.0           0.0  
10199        0.0           0.0  
10200        0.0           0.0  
10201        0.0           0.0  
10202        0.0           0.0  

[10203 rows x 8 columns]

In [114]:
(m, forecast) = make_forecast('AAPL', 365)
forecast

ds      trend  yhat_lower  yhat_upper  trend_lower  trend_upper  \
0     1980-12-12   0.111845   -8.969729   10.136819     0.111845     0.111845   
1     1980-12-15   0.111944   -9.462989    9.633982     0.111944     0.111944   
2     1980-12-16   0.111977   -8.505399    9.780277     0.111977     0.111977   
3     1980-12-17   0.112010   -9.966281    9.363737     0.112010     0.112010   
4     1980-12-18   0.112043   -9.071311   10.293962     0.112043     0.112043   
...          ...        ...         ...         ...          ...          ...   
10563 2022-05-28  99.345905   89.661756  109.229646    98.860339   100.003223   
10564 2022-05-29  99.374872   89.587434  108.833411    98.888563   100.035405   
10565 2022-05-30  99.403839   90.515109  108.832862    98.915286   100.066896   
10566 2022-05-31  99.432805   90.017263  108.919140    98.942793   100.098388   
10567 2022-06-01  99.461772   88.991015  109.528956    98.970300   100.129879   

       additive_terms  additive_terms_lower  additive_terms_upper    weekly  \
0            0.022796              0.022796              0.022796 -0.063862   
1            0.141912              0.141912              0.141912  0.027688   
2            0.152746              0.152746              0.152746  0.028441   
3            0.147644              0.147644              0.147644  0.013199   
4            0.149432              0.149432              0.149432  0.005029   
...               ...                   ...                   ...       ...   
10563       -0.071146             -0.071146             -0.071146 -0.005248   
10564       -0.114051             -0.114051             -0.114051 -0.005248   
10565       -0.126047             -0.126047             -0.126047  0.027688   
10566       -0.171829             -0.171829             -0.171829  0.028441   
10567       -0.234744             -0.234744             -0.234744  0.013199   

       weekly_lower  weekly_upper    yearly  yearly_lower  yearly_upper  \
0         -0.063862     -0.063862  0.086658      0.086658      0.086658   
1          0.027688      0.027688  0.114224      0.114224      0.114224   
2          0.028441      0.028441  0.124305      0.124305      0.124305   
3          0.013199      0.013199  0.134444      0.134444      0.134444   
4          0.005029      0.005029  0.144404      0.144404      0.144404   
...             ...           ...       ...           ...           ...   
10563     -0.005248     -0.005248 -0.065899     -0.065899     -0.065899   
10564     -0.005248     -0.005248 -0.108803     -0.108803     -0.108803   
10565      0.027688      0.027688 -0.153736     -0.153736     -0.153736   
10566      0.028441      0.028441 -0.200270     -0.200270     -0.200270   
10567      0.013199      0.013199 -0.247943     -0.247943     -0.247943   

       multiplicative_terms  multiplicative_terms_lower  \
0                       0.0                         0.0   
1                       0.0                         0.0   
2                       0.0                         0.0   
3                       0.0                         0.0   
4                       0.0                         0.0   
...                     ...                         ...   
10563                   0.0                         0.0   
10564                   0.0                         0.0   
10565                   0.0                         0.0   
10566                   0.0                         0.0   
10567                   0.0                         0.0   

       multiplicative_terms_upper       yhat  
0                             0.0   0.134642  
1                             0.0   0.253857  
2                             0.0   0.264723  
3                             0.0   0.259654  
4                             0.0   0.261476  
...                           ...        ...  
10563                         0.0  99.274758  
10564                         0.0  99.260821  
10565                         0.0  99.277792  
10566       

In [104]:
plot_plotly(m, forecast)

In [105]:
plot_components_plotly(m, forecast)

In [113]:
forecast

ds      trend  yhat_lower  yhat_upper  trend_lower  trend_upper  \
0     1980-12-12   0.111845   -9.291344    9.357810     0.111845     0.111845   
1     1980-12-15   0.111944   -9.633415   10.083393     0.111944     0.111944   
2     1980-12-16   0.111977   -9.658013   10.228735     0.111977     0.111977   
3     1980-12-17   0.112010   -8.786009   10.174575     0.112010     0.112010   
4     1980-12-18   0.112043   -9.351684   10.409016     0.112043     0.112043   
...          ...        ...         ...         ...          ...          ...   
10563 2022-05-28  99.345905   89.345194  108.952586    98.725651    99.788705   
10564 2022-05-29  99.374872   90.093499  108.972431    98.752094    99.821456   
10565 2022-05-30  99.403839   90.220084  109.126278    98.778759    99.854053   
10566 2022-05-31  99.432805   89.438424  109.024597    98.804820    99.886649   
10567 2022-06-01  99.461772   88.942792  109.009491    98.829729    99.919246   

       additive_terms  additive_terms_lower  additive_terms_upper    weekly  \
0            0.022796              0.022796              0.022796 -0.063862   
1            0.141912              0.141912              0.141912  0.027688   
2            0.152746              0.152746              0.152746  0.028441   
3            0.147644              0.147644              0.147644  0.013199   
4            0.149432              0.149432              0.149432  0.005029   
...               ...                   ...                   ...       ...   
10563       -0.071146             -0.071146             -0.071146 -0.005248   
10564       -0.114051             -0.114051             -0.114051 -0.005248   
10565       -0.126047             -0.126047             -0.126047  0.027688   
10566       -0.171829             -0.171829             -0.171829  0.028441   
10567       -0.234744             -0.234744             -0.234744  0.013199   

       weekly_lower  weekly_upper    yearly  yearly_lower  yearly_upper  \
0         -0.063862     -0.063862  0.086658      0.086658      0.086658   
1          0.027688      0.027688  0.114224      0.114224      0.114224   
2          0.028441      0.028441  0.124305      0.124305      0.124305   
3          0.013199      0.013199  0.134444      0.134444      0.134444   
4          0.005029      0.005029  0.144404      0.144404      0.144404   
...             ...           ...       ...           ...           ...   
10563     -0.005248     -0.005248 -0.065899     -0.065899     -0.065899   
10564     -0.005248     -0.005248 -0.108803     -0.108803     -0.108803   
10565      0.027688      0.027688 -0.153736     -0.153736     -0.153736   
10566      0.028441      0.028441 -0.200270     -0.200270     -0.200270   
10567      0.013199      0.013199 -0.247943     -0.247943     -0.247943   

       multiplicative_terms  multiplicative_terms_lower  \
0                       0.0                         0.0   
1                       0.0                         0.0   
2                       0.0                         0.0   
3                       0.0                         0.0   
4                       0.0                         0.0   
...                     ...                         ...   
10563                   0.0                         0.0   
10564                   0.0                         0.0   
10565                   0.0                         0.0   
10566                   0.0                         0.0   
10567                   0.0                         0.0   

       multiplicative_terms_upper       yhat  
0                             0.0   0.134642  
1                             0.0   0.253857  
2                             0.0   0.264723  
3                             0.0   0.259654  
4                             0.0   0.261476  
...                           ...        ...  
10563                         0.0  99.274758  
10564                         0.0  99.260821  
10565                         0.0  99.277792  
10566       